In [1]:
import sys
import os

sys.path.append('*************\\visualize\\taud') # Path for taud
sys.path.append('*************\\visualize\\taud\\DRL_code') # Path for DRL_code

In [2]:
import torch
from torch import nn
from torch.distributions import Normal
import torch.nn.functional as F

import matplotlib.pyplot as plt

import gym 
gym.logger.set_level(40) 
import sac # 自作モジュール(アルゴリズム)
import replay_memory # 自作モジュール

import gym_pathplan # 自作 gym 環境

device=torch.device('cuda')

In [9]:
ENV_ID = 'STLPathPlan-v0'

env = gym.make(ENV_ID)

In [10]:
class SACActor(nn.Module):

    def __init__(self, state_shape, action_shape):
        super().__init__()

        self.net = nn.Sequential(
            nn.Linear(state_shape[0], 256),
            nn.ReLU(inplace=True),
            nn.Linear(256, 256),
            nn.ReLU(inplace=True),
            nn.Linear(256, 2 * action_shape[0]),
        )

    def forward(self, states):
        return torch.tanh(self.net(states).chunk(2, dim=-1)[0])

    def sample(self, states):
        means, log_stds = self.net(states).chunk(2, dim=-1)
        return utility.reparameterize(means, log_stds.clamp(-20, 2))

In [13]:
# 重みの読込をおこなう
baseline_path = 'taud/data/nopreprocess/seed2/SAC_STL_actor_600000.pth'
baseline_param = torch.load(baseline_path)
baseline_policy = SACActor(env.extended_state_space.shape,env.action_space.shape).to(device)
baseline_policy.load_state_dict(baseline_param)

<All keys matched successfully>

In [14]:
# 実際に制御してみる．
evaluate_val = 1.0
state = env.reset_for_test(2.0, 1.0, 0.0)
evaluate_temp = env.evaluate_stl_formula()
evaluate_val = min(evaluate_val,evaluate_temp)
done = False
return_val = 0.0
stl_return_val = 0.0
t = 0
gamma_count = 0
GAMMA = 0.99

while (not done):
    t += 1
    env.render(mode='rgb_array')
    input_state = torch.tensor(state, dtype=torch.float, device=device).unsqueeze_(0) # DNN に入力するため torch.tensor型に
    input_state_ = input_state.cpu().detach().numpy()
    action = baseline_policy(input_state).reshape(-1)
    action_ = action.cpu().detach().numpy() # gym 上では numpy で動くので変換
    next_state, stl_reward, done, true_action = env.step_for_test(action_) # 状態遷移
    
    print("z("+str(t-1)+")="+str(input_state_))
    print("a("+str(t-1)+")="+str(action_))
    print("u("+str(t-1)+")="+str(true_action))
    
    if t == env._max_episode_steps:
        done_masked = False
    else:
        done_masked = done

    evaluate_temp = env.evaluate_stl_formula()
    evaluate_val = min(evaluate_val, evaluate_temp) # \Phi = G\phi
    stl_return_val += (GAMMA**gamma_count)*stl_reward
    gamma_count += 1
    
    # エピソードが終了した場合には，環境をリセットする．
    if done:
        t = 0
        state = env.reset()
    else:
        state = next_state
    
if evaluate_val == 1.0:
    print("この方策はSTL仕様を満たしています")
else:
    print("この方策はSTL仕様を満たしていません")
    
env.close()

z(0)=[[-0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5
   0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5
  -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.
  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5
   0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5
  -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.
  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5
   0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5
  -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.
  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5
   0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5
  -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.
  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5
   0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  0.  -0.5 -1.5  

z(12)=[[-0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0

z(24)=[[-0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0

z(33)=[[-0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0

z(45)=[[-0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0.5        -1.5         0.         -0.5        -1.5         0.
  -0

...

z(948)=[[-12.190187    -1.6225631   -2.6820168  -12.192134    -1.5993847
   -2.652614   -12.17623     -1.6092072   -2.6286469  -12.155922
   -1.5790612   -2.598996   -12.136156    -1.5691884   -2.564411
  -12.126576    -1.5297251   -2.5401642  -12.09103     -1.5160663
   -2.5206196  -12.081092    -1.508188    -2.5082436  -12.076302
   -1.5028124   -2.4961212  -12.086009    -1.5228881   -2.494537
  -12.092954    -1.5535802   -2.487476   -12.089745    -1.5415158
   -2.4828086  -12.082113    -1.5536168   -2.5018888  -12.086287
   -1.5523344   -2.4992008  -12.068724    -1.539559    -2.492213
  -12.066406    -1.558904    -2.4732401  -12.081897    -1.5668977
   -2.455504   -12.08815     -1.5813355   -2.4302032  -12.100429
   -1.5905743   -2.4151978  -12.113135    -1.6068512   -2.4251087
  -12.125667    -1.6214442   -2.4270234  -12.15474     -1.6349622
   -2.4276798  -12.172275    -1.6645344   -2.4217377  -12.197428
   -1.6796571   -2.4322286  -12.230381    -1.7254524   -2.4437652
  -12.2563 

z(960)=[[-12.082113    -1.5536168   -2.5018888  -12.086287    -1.5523344
   -2.4992008  -12.068724    -1.539559    -2.492213   -12.066406
   -1.558904    -2.4732401  -12.081897    -1.5668977   -2.455504
  -12.08815     -1.5813355   -2.4302032  -12.100429    -1.5905743
   -2.4151978  -12.113135    -1.6068512   -2.4251087  -12.125667
   -1.6214442   -2.4270234  -12.15474     -1.6349622   -2.4276798
  -12.172275    -1.6645344   -2.4217377  -12.197428    -1.6796571
   -2.4322286  -12.230381    -1.7254524   -2.4437652  -12.2563
   -1.7449646   -2.4455757  -12.300054    -1.7522011   -2.4348152
  -12.3370905   -1.7766726   -2.4532304  -12.351076    -1.7765515
   -2.4525976  -12.352169    -1.783773    -2.4456115  -12.348538
   -1.8010482   -2.4282296  -12.372115    -1.798058    -2.3854835
  -12.365669    -1.7888992   -2.3434308  -12.335796    -1.7815677
   -2.2872815  -12.323678    -1.7621572   -2.2583776  -12.324883
   -1.7832693   -2.25374    -12.328472    -1.7785951   -2.234417
  -12.341391

z(972)=[[-12.230381    -1.7254524   -2.4437652  -12.2563      -1.7449646
   -2.4455757  -12.300054    -1.7522011   -2.4348152  -12.3370905
   -1.7766726   -2.4532304  -12.351076    -1.7765515   -2.4525976
  -12.352169    -1.783773    -2.4456115  -12.348538    -1.8010482
   -2.4282296  -12.372115    -1.798058    -2.3854835  -12.365669
   -1.7888992   -2.3434308  -12.335796    -1.7815677   -2.2872815
  -12.323678    -1.7621572   -2.2583776  -12.324883    -1.7832693
   -2.25374    -12.328472    -1.7785951   -2.234417   -12.341391
   -1.7912654   -2.2295225  -12.342713    -1.7901138   -2.2154477
  -12.34206     -1.7975255   -2.2100253  -12.348797    -1.8060188
   -2.1912153  -12.3441305   -1.8255978   -2.1703196  -12.3318615
   -1.8385895   -2.1364083  -12.320883    -1.842391    -2.1129756
  -12.322371    -1.8208668   -2.0757403  -12.310207    -1.8161986
   -2.0556607  -12.311485    -1.8021297   -2.0311873  -12.302362
   -1.8046511   -2.0014975  -12.301401    -1.8276697   -1.9911544
  -12.

z(981)=[[-12.335796    -1.7815677   -2.2872815  -12.323678    -1.7621572
   -2.2583776  -12.324883    -1.7832693   -2.25374    -12.328472
   -1.7785951   -2.234417   -12.341391    -1.7912654   -2.2295225
  -12.342713    -1.7901138   -2.2154477  -12.34206     -1.7975255
   -2.2100253  -12.348797    -1.8060188   -2.1912153  -12.3441305
   -1.8255978   -2.1703196  -12.3318615   -1.8385895   -2.1364083
  -12.320883    -1.842391    -2.1129756  -12.322371    -1.8208668
   -2.0757403  -12.310207    -1.8161986   -2.0556607  -12.311485
   -1.8021297   -2.0311873  -12.302362    -1.8046511   -2.0014975
  -12.301401    -1.8276697   -1.9911544  -12.311821    -1.8339559
   -1.9603833  -12.312899    -1.8260432   -1.9551252  -12.298783
   -1.8313082   -1.9409996  -12.315536    -1.827178    -1.9149265
  -12.339048    -1.8404826   -1.9079139  -12.322083    -1.8547697
   -1.9025886  -12.304297    -1.8568139   -1.8743082  -12.304254
   -1.8652629   -1.8566895  -12.299636    -1.8673321   -1.8458223
  -12.2

z(991)=[[-12.320883    -1.842391    -2.1129756  -12.322371    -1.8208668
   -2.0757403  -12.310207    -1.8161986   -2.0556607  -12.311485
   -1.8021297   -2.0311873  -12.302362    -1.8046511   -2.0014975
  -12.301401    -1.8276697   -1.9911544  -12.311821    -1.8339559
   -1.9603833  -12.312899    -1.8260432   -1.9551252  -12.298783
   -1.8313082   -1.9409996  -12.315536    -1.827178    -1.9149265
  -12.339048    -1.8404826   -1.9079139  -12.322083    -1.8547697
   -1.9025886  -12.304297    -1.8568139   -1.8743082  -12.304254
   -1.8652629   -1.8566895  -12.299636    -1.8673321   -1.8458223
  -12.292687    -1.883487    -1.8167845  -12.304371    -1.9009444
   -1.7990161  -12.320723    -1.9120828   -1.7697835  -12.317814
   -1.9253107   -1.7706482  -12.303632    -1.9542109   -1.7600707
  -12.300402    -1.9627092   -1.7433177  -12.296179    -1.9599988
   -1.6931669  -12.300323    -1.9670751   -1.6659528  -12.299495
   -1.9722157   -1.630523   -12.309527    -2.002971    -1.5946692
  -12.32

In [15]:
stl_return_val

-99.99568287525881

In [16]:
ENV_ID = 'STLPathPlan-v1'

env = gym.make(ENV_ID)

In [17]:
# 重みの読込をおこなう
baseline_path = 'taud/data/preprocess/seed2/SAC_STL_actor_600000.pth'
baseline_param = torch.load(baseline_path)
baseline_policy = SACActor(env.extended_state_space.shape,env.action_space.shape).to(device)
baseline_policy.load_state_dict(baseline_param)

<All keys matched successfully>

In [18]:
# 実際に制御してみる．
evaluate_val = 1.0
state = env.reset_for_test(2.0, 1.0, 0.0)
evaluate_temp = env.evaluate_stl_formula()
evaluate_val = min(evaluate_val,evaluate_temp)
done = False
return_val = 0.0
stl_return_val = 0.0
t = 0
gamma_count = 0
GAMMA = 0.99

while (not done):
    t += 1
    env.render(mode='rgb_array')
    input_state = torch.tensor(state, dtype=torch.float, device=device).unsqueeze_(0) # DNN に入力するため torch.tensor型に
    input_state_ = input_state.cpu().detach().numpy()
    action = baseline_policy(input_state).reshape(-1)
    action_ = action.cpu().detach().numpy() # gym 上では numpy で動くので変換
    next_state, stl_reward, done, true_action = env.step_for_test(action_) # 状態遷移
    
    print("z("+str(t-1)+")="+str(input_state_))
    print("a("+str(t-1)+")="+str(action_))
    print("u("+str(t-1)+")="+str(true_action))
    
    if t == env._max_episode_steps:
        done_masked = False
    else:
        done_masked = done

    evaluate_temp = env.evaluate_stl_formula()
    evaluate_val = min(evaluate_val, evaluate_temp) # \Phi = G\phi
    stl_return_val += (GAMMA**gamma_count)*stl_reward
    gamma_count += 1
    
    # エピソードが終了した場合には，環境をリセットする．
    if done:
        t = 0
        state = env.reset()
    else:
        state = next_state
    
if evaluate_val == 1.0:
    print("この方策はSTL仕様を満たしています")
else:
    print("この方策はSTL仕様を満たしていません")
    
env.close()

z(0)=[[-0.5 -1.5  0.  -0.5 -0.5  0.   0.   0.   0.   0.   0.   0.   0.   0.
   0.   0.   0.   0.   0.   0.   0.   0.   0.   0.   0. ]]
a(0)=[0.95971006 0.98925084]
u(0)=[0. 0.]
z(1)=[[-0.4866946  -1.5035166   0.0035011  -0.5        -0.5         0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.95971006
   0.98925084]]
a(1)=[0.97539    0.94642586]
u(1)=[0. 0.]
z(2)=[[-0.49377465 -1.5160851   0.00857491 -0.5        -0.5         0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.95971006  0.98925084  0.97539
   0.94642586]]
a(2)=[0.7793193  0.76764834]
u(2)=[0. 0.]
z(3)=[[-0.47987297 -1.5198412   0.02979494 -0.5        -0.5         0.
   0.          0.          0.          0.          0.          0.
   0.          0.  

z(25)=[[ 0.9250101  -0.753836    0.45666555 -0.5        -0.5         0.9600884
  -0.24564846  0.9646452  -0.36706626  0.9644023  -0.50451934  0.967675
  -0.5485796   0.96254957 -0.64420754  0.9585449  -0.6927483   0.95013237
  -0.7641263   0.93440855 -0.8221231   0.9091093  -0.8628504   0.8578311
  -0.90734404]]
a(25)=[ 0.8002393 -0.9313167]
u(25)=[ 0.967675  -0.5485796]
z(26)=[[ 1.0161684  -0.7218557   0.40207392 -0.5        -0.5         0.9646452
  -0.36706626  0.9644023  -0.50451934  0.967675   -0.5485796   0.96254957
  -0.64420754  0.9585449  -0.6927483   0.95013237 -0.7641263   0.93440855
  -0.8221231   0.9091093  -0.8628504   0.8578311  -0.90734404  0.8002393
  -0.9313167 ]]
a(26)=[ 0.70619917 -0.9368708 ]
u(26)=[ 0.96254957 -0.64420754]
z(27)=[[ 1.1194967  -0.6976147   0.33381864 -0.5        -0.5         0.9644023
  -0.50451934  0.967675   -0.5485796   0.96254957 -0.64420754  0.9585449
  -0.6927483   0.95013237 -0.7641263   0.93440855 -0.8221231   0.9091093
  -0.8628504   0.8578

z(49)=[[ 1.5412503  -0.01886546 -1.3246037  -0.5         0.5        -0.9540363
  -0.65671873 -0.972366   -0.62265784 -0.9756373  -0.5253378  -0.9790463
  -0.33521202 -0.9813248  -0.25693533 -0.97831225 -0.22308215 -0.97755677
  -0.16436946 -0.97592205 -0.06167155 -0.9805727  -0.02189879 -0.9822739
   0.02457922]]
a(49)=[-0.98569274  0.1076371 ]
u(49)=[-0.9790463  -0.33521202]
z(50)=[[ 1.5296544   0.07328518 -1.3585299  -0.5         0.49       -0.972366
  -0.62265784 -0.9756373  -0.5253378  -0.9790463  -0.33521202 -0.9813248
  -0.25693533 -0.97831225 -0.22308215 -0.97755677 -0.16436946 -0.97592205
  -0.06167155 -0.9805727  -0.02189879 -0.9822739   0.02457922 -0.98569274
   0.1076371 ]]
a(50)=[-0.98873895  0.19877505]
u(50)=[-0.9813248  -0.25693533]
z(51)=[[ 1.5196146   0.1760852  -1.3902273  -0.5         0.48       -0.9756373
  -0.5253378  -0.9790463  -0.33521202 -0.9813248  -0.25693533 -0.97831225
  -0.22308215 -0.97755677 -0.16436946 -0.97592205 -0.06167155 -0.9805727
  -0.02189879 -0

z(74)=[[ 8.7699914e-01  2.0441124e+00 -6.0820919e-01  4.0000001e-01
   2.5000000e-01 -4.6775961e-01  5.1778382e-01 -3.6539981e-01
   4.5303139e-01 -2.0301904e-01  4.1945046e-01  1.7894227e-03
   3.5161102e-01  1.2217774e-01  1.6132277e-01  2.5176227e-01
  -3.4669423e-03  3.8838574e-01 -9.9480100e-02  4.9547204e-01
  -2.1268480e-01  6.2214756e-01 -1.7362307e-01  6.3922167e-01
  -1.9548577e-01]]
a(74)=[ 0.6725328  -0.17815557]
u(74)=[0.00178942 0.35161102]
z(75)=[[ 8.7320840e-01  2.0512323e+00 -5.6355184e-01  3.8999999e-01
   2.3999999e-01 -3.6539981e-01  4.5303139e-01 -2.0301904e-01
   4.1945046e-01  1.7894227e-03  3.5161102e-01  1.2217774e-01
   1.6132277e-01  2.5176227e-01 -3.4669423e-03  3.8838574e-01
  -9.9480100e-02  4.9547204e-01 -2.1268480e-01  6.2214756e-01
  -1.7362307e-01  6.3922167e-01 -1.9548577e-01  6.7253280e-01
  -1.7815557e-01]]
a(75)=[ 0.64948314 -0.16302782]
u(75)=[0.12217774 0.16132277]
z(76)=[[ 8.9153981e-01  2.0465171e+00 -5.6490016e-01  3.8000000e-01
   2.3000000e-

z(99)=[[ 1.4925272e+00  1.6033399e+00 -5.9415257e-01  5.0000000e-01
  -4.4408921e-16  1.4494310e-01 -4.8127625e-02  3.1115001e-01
   3.4239457e-03  2.7588052e-01 -5.8421601e-02  2.4716109e-01
  -1.4089318e-01  4.4287339e-01 -1.5720625e-01  4.5217314e-01
  -1.5476713e-01  4.9500066e-01 -1.5044267e-01  5.2354980e-01
  -2.3637971e-01  6.9205970e-01 -1.8353401e-01  7.2095704e-01
  -3.0701602e-01]]
a(99)=[ 0.69268817 -0.2584632 ]
u(99)=[ 0.24716109 -0.14089318]
z(100)=[[ 1.5038253   1.5930998  -0.6002994   0.5        -0.01        0.31115
   0.00342395  0.27588052 -0.0584216   0.24716109 -0.14089318  0.4428734
  -0.15720625  0.45217314 -0.15476713  0.49500066 -0.15044267  0.5235498
  -0.23637971  0.6920597  -0.18353401  0.72095704 -0.30701602  0.69268817
  -0.2584632 ]]
a(100)=[ 0.78884846 -0.35132855]
u(100)=[ 0.4428734  -0.15720625]
z(101)=[[ 1.541406    1.5662848  -0.6213984   0.5        -0.02        0.27588052
  -0.0584216   0.24716109 -0.14089318  0.4428734  -0.15720625  0.45217314
  -0

...

z(891)=[[ 1.2646561   1.6393301  -0.938181    0.5        -0.02       -0.944501
   0.20584771 -0.8971233   0.35481837 -0.8622396   0.3706488  -0.71317554
   0.29855084 -0.5114698   0.23500602 -0.63641757  0.30027145  0.5371423
   0.8710077   0.865206    0.64706206  0.72206867  0.15224952  0.7405654
   0.18354906]]
a(891)=[0.57873654 0.20722347]
u(891)=[-0.71317554  0.29855084]
z(892)=[[ 1.2175997   1.6933498  -0.9016631   0.49       -0.03       -0.8971233
   0.35481837 -0.8622396   0.3706488  -0.71317554  0.29855084 -0.5114698
   0.23500602 -0.63641757  0.30027145  0.5371423   0.8710077   0.865206
   0.64706206  0.72206867  0.15224952  0.7405654   0.18354906  0.57873654
   0.20722347]]
a(892)=[0.8773279  0.08672319]
u(892)=[-0.5114698   0.23500602]
z(893)=[[ 1.1804724   1.7181599  -0.8836871   0.48       -0.04       -0.8622396
   0.3706488  -0.71317554  0.29855084 -0.5114698   0.23500602 -0.63641757
   0.30027145  0.5371423   0.8710077   0.865206    0.64706206  0.72206867
   0.15224952 

a(920)=[ 0.8947574 -0.7052282]
u(920)=[ 0.84807336 -0.41275534]
z(921)=[[ 2.5069177   0.13967639 -1.3484095   0.34       -0.32        0.81391793
  -0.48827973  0.667603   -0.28112295  0.84807336 -0.41275534  0.6544793
  -0.437915    0.7363614  -0.39220285  0.78909314 -0.46386167  0.8190956
  -0.50381535  0.8761646  -0.5057739   0.84117955 -0.5619728   0.8947574
  -0.7052282 ]]
a(921)=[ 0.83834624 -0.59945333]
u(921)=[ 0.6544793 -0.437915 ]
z(922)=[[ 2.5053854   0.08578659 -1.4066249   0.33       -0.33        0.667603
  -0.28112295  0.84807336 -0.41275534  0.6544793  -0.437915    0.7363614
  -0.39220285  0.78909314 -0.46386167  0.8190956  -0.50381535  0.8761646
  -0.5057739   0.84117955 -0.5619728   0.8947574  -0.7052282   0.83834624
  -0.59945333]]
a(922)=[ 0.8484054  -0.70091397]
u(922)=[ 0.7363614  -0.39220285]
z(923)=[[ 2.520832    0.01264071 -1.4449595   0.32       -0.34        0.84807336
  -0.41275534  0.6544793  -0.437915    0.7363614  -0.39220285  0.78909314
  -0.46386167  0.819

z(942)=[[ 2.4383616  -0.68527114 -1.9953903   0.13        0.5        -0.6139773
   0.02113664 -0.5840318   0.02485308 -0.62495744  0.11321621 -0.614576
   0.32039747 -0.72923887  0.4910149  -0.8784935   0.6803374  -0.93290365
   0.7473156  -0.9324207   0.75345993 -0.9619555   0.7664732  -0.9543576
   0.7240851 ]]
a(942)=[-0.9666372  0.813786 ]
u(942)=[-0.614576    0.32039747]
z(943)=[[ 2.4605167  -0.656874   -1.9409807   0.12        0.5        -0.5840318
   0.02485308 -0.62495744  0.11321621 -0.614576    0.32039747 -0.72923887
   0.4910149  -0.8784935   0.6803374  -0.93290365  0.7473156  -0.9324207
   0.75345993 -0.9619555   0.7664732  -0.9543576   0.7240851  -0.9666372
   0.813786  ]]
a(943)=[-0.9796872  0.8681245]
u(943)=[-0.72923887  0.4910149 ]
z(944)=[[ 2.473276   -0.5823992  -1.8804348   0.11        0.5        -0.62495744
   0.11321621 -0.614576    0.32039747 -0.72923887  0.4910149  -0.8784935
   0.6803374  -0.93290365  0.7473156  -0.9324207   0.75345993 -0.9619555
   0.7664732  

z(965)=[[ 1.7275918   0.99986225 -0.24705684 -0.1         0.29       -0.8098357
   0.5811335  -0.758723    0.4960365  -0.70301086  0.42920336 -0.6566019
   0.32910803 -0.6231493   0.18839794 -0.59960747  0.05651913 -0.56180346
  -0.08246204 -0.5156352  -0.20216861 -0.390684   -0.26459506 -0.33006006
  -0.3347808 ]]
a(965)=[-0.20227128 -0.3534015 ]
u(965)=[-0.6566019   0.32910803]
z(966)=[[ 1.6836932   1.0240265  -0.22511016 -0.11        0.28       -0.758723
   0.4960365  -0.70301086  0.42920336 -0.6566019   0.32910803 -0.6231493
   0.18839794 -0.59960747  0.05651913 -0.56180346 -0.08246204 -0.5156352
  -0.20216861 -0.390684   -0.26459506 -0.33006006 -0.3347808  -0.20227128
  -0.3534015 ]]
a(966)=[-0.13535653 -0.34980026]
u(966)=[-0.6231493   0.18839794]
z(967)=[[ 1.6017954   1.0325027  -0.21381493 -0.12        0.27       -0.70301086
   0.42920336 -0.6566019   0.32910803 -0.6231493   0.18839794 -0.59960747
   0.05651913 -0.56180346 -0.08246204 -0.5156352  -0.20216861 -0.390684
  -0.2645

z(987)=[[ 1.9605197   0.73412406 -0.7989659  -0.32        0.07        0.77907044
  -0.59008765  0.53800833 -0.66766155  0.17047039 -0.60448885 -0.33453676
  -0.41140297 -0.34727862 -0.2628207  -0.44470924 -0.28941587 -0.4827815
  -0.3425915  -0.7883885  -0.3027528  -0.8868842  -0.43068913 -0.9359063
  -0.2467589 ]]
a(987)=[-0.93838894 -0.18870051]
u(987)=[-0.33453676 -0.41140297]
z(988)=[[ 1.9473525   0.76860976 -0.8468271  -0.33        0.06        0.53800833
  -0.66766155  0.17047039 -0.60448885 -0.33453676 -0.41140297 -0.34727862
  -0.2628207  -0.44470924 -0.28941587 -0.4827815  -0.3425915  -0.7883885
  -0.3027528  -0.8868842  -0.43068913 -0.9359063  -0.2467589  -0.93838894
  -0.18870051]]
a(988)=[-0.97614664 -0.05569312]
u(988)=[-0.34727862 -0.2628207 ]
z(989)=[[ 1.9242301   0.8071698  -0.86628914 -0.34        0.05        0.17047039
  -0.60448885 -0.33453676 -0.41140297 -0.34727862 -0.2628207  -0.44470924
  -0.28941587 -0.4827815  -0.3425915  -0.7883885  -0.3027528  -0.8868842
  -0.